In [1]:
from fastai2.vision.all import *
from tqdm.notebook import tqdm

In [2]:
HATE_IMAGES = Path('/home/jupyter/mmf_data/datasets/hateful_memes/defaults/images')

In [92]:
PHASE_2 = Path('/home/jupyter/hate_phase2')
train = pd.read_json(PHASE_2/'train.jsonl', lines=True)
dev_seen = pd.read_json(PHASE_2/'dev_seen.jsonl', lines=True)
dev_unseen = pd.read_json(PHASE_2/'dev_unseen.jsonl', lines=True)
df = pd.concat([train, dev_seen])

In [4]:
model = resnet50(pretrained=True).cuda()
model.eval()
hasher = nn.Sequential(*list(model.children())[:-1])

In [5]:
def to_vector(b):
    if len(b.shape) == 3: b = b.unsqueeze(0)
    with torch.no_grad():
        res =hasher(b).squeeze() 
    return res

In [6]:
'''img_pipe = Pipeline([PILImage.create, resize, ToTensor(), IntToFloatTensor])

def load_tensor(img_path):
    img_path = HATE_IMAGES/img_path
    img = PILImage.create(img_path)
    return IntToFloatTensor()(ToTensor()(img)).cuda()

%%time
vectors =[]
for _,row in tqdm(df.iterrows()):
    vectors.append(to_vector(load_tensor(row['img'])))

torch.save(all_v, 'all_vectors.pt')'''

"img_pipe = Pipeline([PILImage.create, resize, ToTensor(), IntToFloatTensor])\n\ndef load_tensor(img_path):\n    img_path = HATE_IMAGES/img_path\n    img = PILImage.create(img_path)\n    return IntToFloatTensor()(ToTensor()(img)).cuda()\n\n%%time\nvectors =[]\nfor _,row in tqdm(df.iterrows()):\n    vectors.append(to_vector(load_tensor(row['img'])))\n\ntorch.save(all_v, 'all_vectors.pt')"

In [93]:
all_v = torch.load('all_vectors.pt')
all_v.shape

torch.Size([10000, 2048])

In [94]:
def distances_p1(x, b):
    return (b-x).norm(p=1, dim=1)

def distances_p2(x, b):
    return (b-x).norm(p=2, dim=1)
    
def distances_cos(x, b):
    return 1 -F.cosine_similarity(x.unsqueeze(0),b, dim=1)

In [95]:
trainV = all_v[:8500]
validV = all_v[8500:9000]

In [96]:
all_dists = [distances_cos(all_v[i], trainV) for i in range(len(all_v))]

In [97]:
def get_nearest(start_idx, distances):
    near = []
    for idx, dists in enumerate(distances[start_idx:]):
        values, indices =dists.topk(3, largest=False, sorted=True)
        near.append(torch.cat([torch.tensor(idx+start_idx).view(1),indices.cpu()]))
    return torch.cat(near).view(-1,4)

In [112]:
def knn(k):
    match = 0
    for idx, x in enumerate(validV):
        dists = distances_cos(x, trainV)
        values, indices =dists.topk(k, largest=False, sorted=True)
        count =[0,0]
        for sim_idx in indices:
            lab = df.iloc[sim_idx.cpu().item()].label
            count[lab] +=1
        y = np.argmax(count)
        y_hat = df.iloc[idx+8500].label
        match += (y==y_hat)
    return match / len(validV)

In [102]:
N = get_nearest(8500, all_dists)
N

tensor([[8500, 7425, 1607, 4776],
        [8501, 1175, 4301,  670],
        [8502, 4827, 6260, 7144],
        ...,
        [9997, 1129, 8077, 3145],
        [9998, 1614, 1717, 4551],
        [9999, 6229,  819, 5578]])

In [103]:
def display_img(img_path, ax, caption, color):
    ax.imshow(PIL.Image.open(img_path))
    ax.axis('off')
    ax.set_title(caption, color=color,fontdict={'fontsize': 20, 'fontweight': 'medium'}) 

In [106]:
import PIL
def show_nearest(img_idxs):
    n,m = img_idxs.shape
    
    _,axs = plt.subplots(n//2,m, figsize=(10*m,10*n))
    get_ax = iter(axs.flatten())
    for imgs_row in img_idxs:
        y1 = df.iloc[imgs_row[0].cpu().item()].label
        y2 = df.iloc[imgs_row[1].cpu().item()].label
        if y1!=y2: continue
        for i, idx in enumerate(imgs_row):
            ax = next(get_ax)
            row = df.iloc[idx.item()]
            img_path = HATE_IMAGES / row['img']
            clr = 'red' if row['label']==1 else 'green'
            if i==0: txt = '0'
            else: txt = f'{all_dists[imgs_row[0]][imgs_row[i]]:.2f}'
            display_img(img_path, ax, txt, clr)

In [108]:
show_nearest(N[:50])